In [1]:
using ModelingToolkit

┌ Info: Precompiling ModelingToolkit [961ee093-0014-501f-94e3-6117800e7a78]
└ @ Base loading.jl:1313


$$ T_D (n, e_c) = J \frac{d^2 \theta_0 (t)}{dt^2} + B \frac{d \theta_0 (t)}{dt} $$

- $T_D$ : Torque Developed
- $J$ : Inertia
- $B$ : Dampening


Kim, et. al. 2011:

$$ \dot\theta = \omega$$
$$ \dot\omega = \frac{1}{J} ( -K_m i_a sin(N_r \theta) + K_m i_b cos(N_r \theta) - B \omega - \tau)$$
$$ \dot i_a = \frac{1}{L} ( v_a - R i_a + K_m sin(N_r \theta))$$
$$ \dot i_b = \frac{1}{L} ( v_b - R i_b - K_m cos(N_r \theta))$$


In [12]:
using ModelingToolkit, OrdinaryDiffEq

@parameters J Km Nr B τ R va vb L
@variables θ(t) ω(t) ia(t) ib(t)
D = Differential(t)

eqs = [D(θ) ~ ω,
       D(ω) ~ (1/J)*(-Km*ia*sin(Nr*θ) + Km*ib*cos(Nr*θ) - B * ω - τ),
       D(ia) ~ (1/L)*(va - R * ia + Km *ω*sin(Nr*θ)),
       D(ib) ~ (1/L)*(vb - R * ib - Km *ω*cos(Nr*θ))]

sys = ODESystem(eqs)


ODESystem(Equation[Equation(Differential(θ(t)), ω(t)), Equation(Differential(ω(t)), (1 / J) * ((((((-Km) * ia(t)) * sin(Nr * θ(t))) + ((Km * ib(t)) * cos(Nr * θ(t)))) - (B * ω(t))) - τ)), Equation(Differential(ia(t)), (1 / L) * ((va - (R * ia(t))) + ((Km * ω(t)) * sin(Nr * θ(t))))), Equation(Differential(ib(t)), (1 / L) * ((vb - (R * ib(t))) - ((Km * ω(t)) * cos(Nr * θ(t)))))], t, Term{Real}[θ(t), ω(t), ia(t), ib(t)], Sym{ModelingToolkit.Parameter{Real}}[Km, τ, J, Nr, B, L, R, va, vb], Num[], Equation[], Base.RefValue{Vector{Num}}(Num[]), Base.RefValue{Any}(Matrix{Num}(undef, 0, 0)), Base.RefValue{Matrix{Num}}(Matrix{Num}(undef, 0, 0)), Base.RefValue{Matrix{Num}}(Matrix{Num}(undef, 0, 0)), Symbol("##ODESystem#265"), ODESystem[])

In [32]:
u0 = [θ => 1.0,
      ω => 1.0,
      ia => 1.0,
      ib => 1.0]

p  = [J => 8e-5, # kg⋅m²
      Km => 0.51, # N⋅m/A
      Nr => 50.0,
      B => 0.001,
      va => 12,
      vb => 12,
      R  => 1.65,
      τ => 0,
      L => 2.8]

9-element Vector{Pair{Num, Float64}}:
  J => 8.0e-5
 Km => 0.51
 Nr => 50.0
  B => 0.001
 va => 12.0
 vb => 12.0
  R => 1.65
  τ => 0.0
  L => 2.8

In [34]:
tspan = (0.0,10.0)
prob = ODEProblem(sys,u0,tspan,p,jac=true)
sol = solve(prob,Tsit5())

retcode: Success
Interpolation: specialized 4th order "free" interpolation
t: 11799-element Vector{Float64}:
  0.0
  0.00025602294511409604
  0.0007036469548782035
  0.0012992691070343454
  0.002088628385049319
  0.0029417587140941987
  0.0038452518813761175
  0.005009618018161188
  0.006026958118543582
  0.0072928364713901244
  0.008511427036451762
  0.009814977620385437
  0.011075834365784241
  ⋮
  9.991070142699682
  9.991829843300325
  9.992681278857711
  9.993402560166208
  9.994353651257269
  9.995048195861662
  9.995987262154687
  9.996643919724692
  9.997666505487075
  9.998270194148603
  9.999341598246101
 10.0
u: 11799-element Vector{Vector{Float64}}:
 [1.0, 1.0, 1.0, 1.0]
 [1.0005109012514464, 2.985303944426745, 1.0009230343377797, 1.0008562058780035]
 [1.0026012753813056, 6.312757510400683, 1.0025061850741759, 1.002136524688009]
 [1.0075449439071713, 10.12906630951215, 1.004695977349535, 1.0034391078692395]
 [1.0169071186609733, 13.083482116241663, 1.0081835493184763, 1.004

In [35]:
using Plots; plot(sol)